# Realized Cap
Author: [@typerbole](https://twitter.com/typerbole), [GitHub](https://github.com/ty-perbole), [stack-stats.com](http://www.stack-stats.com)

In the [previous tutorial](https://ty-perbole.github.io/stack-stats/02_HODLWaves.html) we dove into working with on-chain data and generated the HODL wave charts popularized by [Dhruv Bansal at Unchained Capital](https://unchained-capital.com/blog/hodl-waves-1/). We experimented with using different weightings for calculating the relative width of each age band:
1. BTC value weighted: one Sat, one vote (original HODL waves chart)
2. Flat weighting: one UTXO, one vote (UTXO count)
3. Flat weighting, filtered: one UTXO > 0.01 BTC, one vote (UTXO count > 0.01 BTC)
4. Realized cap weighted: $1 cost basis, one vote (at market price from time of UTXO creation)

In this notebook we're going to tackle the fourth weighting which is a little more complicated.

## Realized Cap methodology

The history and methodology of Realized Cap is discussed in the [original blog post](https://coinmetrics.io/realized-capitalization/) by CoinMetrics. I suggest you read that post before proceeding with this notebook so you have a thorough understanding of what we're calculating.

Realized cap is a Market Cap analogue that values each UTXO at the price when it was created on-chain, rather than the current price. It typically lags Market Cap and is roughly an estimate of the cost basis of all Bitcoin hodlers.

## ${Realized\ Cap}=\sum_{}UTXO\ Value\ (BTC) * BTC\ price\ at\ UTXO\ creation$

Realized Cap is a useful input into some of the valuation ratios discussed in the earlier [ratios tutorial](https://ty-perbole.github.io/stack-stats/01_BitcoinNetworkRatios.html).

## Calculation

The calculation for Realized Cap is an extension of the work we did for [HODL Waves](https://ty-perbole.github.io/stack-stats/02_HODLWaves.html), so I recommend going go through that tutorial first before trying this one.

Realized Cap requires a BTC price feed, which isn't available on BigQuery public data, so we'll need to upload the data ourselves. Luckily this is pretty easy.

First we need to download the latest CoinMetrics community data:

In [8]:
# import os
# try:
#     os.remove("btc.csv")
# except FileNotFoundError:
#     pass
# !wget https://coinmetrics.io/newdata/btc.csv

--2020-05-12 08:58:51--  https://coinmetrics.io/newdata/btc.csv
Resolving coinmetrics.io (coinmetrics.io)... 104.26.15.66, 104.26.14.66
Connecting to coinmetrics.io (coinmetrics.io)|104.26.15.66|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 2478678 (2.4M) [application/octet-stream]
Saving to: ‘btc.csv’

btc.csv             100%[===================>]   2.36M  12.9MB/s    in 0.2s    

2020-05-12 08:58:52 (12.9 MB/s) - ‘btc.csv’ saved [2478678/2478678]



The CoinMetrics data should now be located in the Stack Stats directory on your computer as btc.csv.

Now you just have to create a new BigQuery table via the [web UI](https://bigquery.cloud.google.com/) as such: 

![Transactions Table Schema](img/cm_bigquery.png)

Once you hit "Create new table" you simply have to upload the btc.csv file, hit "Automatically detect" under Schema, the hit Create Table on the bottom. If will upload the file and you will then have a BigQuery table with the CoinMetrics community data. I named my table "cm_btc" under my private "bitcoin" BigQuery dataset.

Now that we have that set up, we can start to build our query. Since we are working off the query we built for the HODL Waves tutorial, I will not explain anything that was already covered there.

In [2]:
QUERY = '''
WITH

-- Outputs subquery: contains relevant information about a given output.
-- A TXO is created when it is an output of a transaction, so this contains
-- metadata about the TXO creation
output AS (
  SELECT
    transactions.HASH AS transaction_hash,
    transactions.block_number AS created_block_number,
    transactions.block_timestamp AS created_block_ts,
    outputs.index AS output_index,
    outputs.value AS output_value
  FROM
    `bigquery-public-data.crypto_bitcoin.transactions` AS transactions,
    transactions.outputs AS outputs
    ),

-- Inputs subquery: contains relevant information about a given input.
-- A TXO is consumed when it is the input to a transaction, so this metadata
-- tells us about when a TXO is spent or destroyed
input AS (
  SELECT
    transactions.hash AS spending_transaction_hash,
    inputs.spent_transaction_hash AS spent_transaction_hash,
    transactions.block_number AS destroyed_block_number,
    transactions.block_timestamp AS destroyed_block_ts,
    inputs.spent_output_index,
    inputs.value AS input_value
  FROM
    `bigquery-public-data.crypto_bitcoin.transactions` AS transactions,
    transactions.inputs AS inputs
    ),
'''

In [3]:
QUERY += '''
-- Now we can add the table we created and get the daily USD price of bitcoin
cm AS (
SELECT
  date,
  PriceUSD
FROM
-- ** YOU WILL HAVE TO REPLACE THE PROJECT NAME HERE TO REFLECT YOUR OWN BIGQUERY TABLE **
  `replace_this_project.bitcoin.cm_btc`),
'''

In [4]:
QUERY += '''
-- txo subquery: joins outputs to inputs so that we know when/if a TXO is spent.
-- NEW: we also join the price data and calculate the cost basis of each TXO
txo AS (
  SELECT
    output.transaction_hash,
    output.created_block_number,
    DATETIME(output.created_block_ts) AS created_block_ts,
    -- Any field from the input table will be NULL if the TXO remains unspent.
    input.spending_transaction_hash,
    input.spent_transaction_hash,
    input.destroyed_block_number,
    DATETIME(input.destroyed_block_ts) AS destroyed_block_ts,
    output.output_value,
    output.output_value * cm.PriceUSD / 100000000 AS output_cost_basis_usd,
    cm.PriceUSD AS output_cost_basis_price
  FROM
    output
  -- Use Left Join, as not all outputs will be linked as inputs in future transactions if they remain unspent.
  LEFT JOIN
    input
  ON
    -- Join an output to a future input based on the output transaction hash
    -- matching the spent transaction hash of the input
    output.transaction_hash = input.spent_transaction_hash
    -- Also make sure the output index matches within the transaction hash
    AND output.output_index = input.spent_output_index
  -- Get the price data from our cm table with coinmetrics price data
  LEFT JOIN
    cm
  ON
  -- Join the price data onto the output creation block ts, to get the price at the time of output creation (cost basis)
    DATE(output.created_block_ts) = cm.date
  ),
'''

In [5]:
QUERY += '''
-- blocks subquery: for each date get the final block for that date
-- NEW: we also join the price data so that we can see the price at each block
blocks AS (
  SELECT
    DATE(blocks.timestamp) AS date,
    -- Get last block per day
    MAX(blocks.number) AS block_number,
    MAX(DATETIME(blocks.timestamp)) AS block_ts,
    cm.PriceUSD AS price_usd
  FROM
    `bigquery-public-data.crypto_bitcoin.blocks` AS blocks
  LEFT JOIN
    cm
  ON
    cm.date = DATE(blocks.timestamp)
  GROUP BY
    date, price_usd)
'''

In [6]:
QUERY += '''
-- final data aggregation query: join txo with blocks, keeping only txo
-- that were created and unspent as of that block, then bucket the txo
-- by age and sum the txo value per bucket per that day
-- NEW: Last grouping of SUM() columns, where we sum the output_cost_basis_usd column
--      from the txo table to get realized cap!
SELECT
  -- Time series metadata
  blocks.date AS date,
  blocks.block_number AS block_number,
  blocks.block_ts AS block_ts,
  blocks.price_usd AS price_usd,

-- BTC Value Weighting
  -- Total UTXO value on that date
  SUM(txo.output_value) AS total_utxo_value,
  -- Our HODL Waves buckets, counting value of UTXO
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 1, txo.output_value, 0)) AS utxo_value_under_1d,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 1
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 7,
         txo.output_value, 0)) AS utxo_value_1d_1w,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 7
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 28,
         txo.output_value, 0)) AS utxo_value_1w_1m,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 28
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 28 * 3,
         txo.output_value, 0)) AS utxo_value_1m_3m,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 28 * 3
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 28 * 6,
         txo.output_value, 0)) AS utxo_value_3m_6m,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 28 * 6
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 28 * 12,
         txo.output_value, 0)) AS utxo_value_6m_12m,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 28 * 12
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 28 * 18,
         txo.output_value, 0)) AS utxo_value_12m_18m,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 28 * 18
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 28 * 24,
         txo.output_value, 0)) AS utxo_value_18m_24m,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 28 * 12 * 2
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 28 * 12 * 3,
         txo.output_value, 0)) AS utxo_value_2y_3y,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 28 * 12 * 3
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 28 * 12 * 5,
         txo.output_value, 0)) AS utxo_value_3y_5y,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 28 * 12 * 5
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 28 * 12 * 8,
         txo.output_value, 0)) AS utxo_value_5y_8y,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 28 * 12 * 8,
         txo.output_value, 0)) AS utxo_value_greater_8y,

-- Flat Weighting
  -- Total UTXO count on that date
  SUM(1) AS total_utxo_count,
  -- Our HODL Waves buckets, counting number of UTXO
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 1, 1, 0)) AS utxo_count_under_1d,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 1
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 7,
         1, 0)) AS utxo_count_1d_1w,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 7
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 28,
         1, 0)) AS utxo_count_1w_1m,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 28
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 28 * 3,
         1, 0)) AS utxo_count_1m_3m,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 28 * 3
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 28 * 6,
         1, 0)) AS utxo_count_3m_6m,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 28 * 6
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 28 * 12,
         1, 0)) AS utxo_count_6m_12m,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 28 * 12
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 28 * 18,
         1, 0)) AS utxo_count_12m_18m,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 28 * 18
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 28 * 24,
         1, 0)) AS utxo_count_18m_24m,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 28 * 12 * 2
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 28 * 12 * 3,
         1, 0)) AS utxo_count_2y_3y,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 28 * 12 * 3
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 28 * 12 * 5,
         1, 0)) AS utxo_count_3y_5y,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 28 * 12 * 5
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 28 * 12 * 8,
         1, 0)) AS utxo_count_5y_8y,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 28 * 12 * 8,
         1, 0)) AS utxo_count_greater_8y,

-- Flat weighting, filtered
  -- Total UTXO count on that date (> 0.01 BTC)
  SUM(IF(txo.output_value / 100000000 > 0.01, 1, 0)) AS total_utxo_count_filter,
  -- Our HODL Waves buckets, counting number of UTXO (> 0.01 BTC)
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 1
         AND txo.output_value / 100000000 >= 0.01,
         1, 0)) AS utxo_count_filter_under_1d,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 1
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 7
         AND txo.output_value / 100000000 >= 0.01,
         1, 0)) AS utxo_count_filter_1d_1w,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 7
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 28
         AND txo.output_value / 100000000 >= 0.01,
         1, 0)) AS utxo_count_filter_1w_1m,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 28
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 28 * 3
         AND txo.output_value / 100000000 >= 0.01,
         1, 0)) AS utxo_count_filter_1m_3m,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 28 * 3
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 28 * 6
         AND txo.output_value / 100000000 >= 0.01,
         1, 0)) AS utxo_count_filter_3m_6m,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 28 * 6
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 28 * 12
         AND txo.output_value / 100000000 >= 0.01,
         1, 0)) AS utxo_count_filter_6m_12m,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 28 * 12
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 28 * 18
         AND txo.output_value / 100000000 >= 0.01,
         1, 0)) AS utxo_count_filter_12m_18m,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 28 * 18
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 28 * 24
         AND txo.output_value / 100000000 >= 0.01,
         1, 0)) AS utxo_count_filter_18m_24m,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 28 * 12 * 2
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 28 * 12 * 3
         AND txo.output_value / 100000000 >= 0.01,
         1, 0)) AS utxo_count_filter_2y_3y,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 28 * 12 * 3
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 28 * 12 * 5
         AND txo.output_value / 100000000 >= 0.01,
         1, 0)) AS utxo_count_filter_3y_5y,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 28 * 12 * 5
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 28 * 12 * 8
         AND txo.output_value / 100000000 >= 0.01,
         1, 0)) AS utxo_count_filter_5y_8y,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 28 * 12 * 8
         AND txo.output_value / 100000000 >= 0.01,
         1, 0)) AS utxo_count_filter_greater_8y,

-- BTC USD Value (Realized Cap) Weighting
  -- Realized Cap on that date
  SUM(txo.output_cost_basis_usd) AS realized_cap,
  -- Our HODL Waves buckets, counting value of UTXO
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 1, txo.output_cost_basis_usd, 0)) AS utxo_realcap_under_1d,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 1
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 7,
         txo.output_cost_basis_usd, 0)) AS utxo_realcap_1d_1w,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 7
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 28,
         txo.output_cost_basis_usd, 0)) AS utxo_realcap_1w_1m,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 28
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 28 * 3,
         txo.output_cost_basis_usd, 0)) AS utxo_realcap_1m_3m,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 28 * 3
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 28 * 6,
         txo.output_cost_basis_usd, 0)) AS utxo_realcap_3m_6m,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 28 * 6
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 28 * 12,
         txo.output_cost_basis_usd, 0)) AS utxo_realcap_6m_12m,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 28 * 12
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 28 * 18,
         txo.output_cost_basis_usd, 0)) AS utxo_realcap_12m_18m,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 28 * 18
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 28 * 24,
         txo.output_cost_basis_usd, 0)) AS utxo_realcap_18m_24m,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 28 * 12 * 2
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 28 * 12 * 3,
         txo.output_cost_basis_usd, 0)) AS utxo_realcap_2y_3y,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 28 * 12 * 3
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 28 * 12 * 5,
         txo.output_cost_basis_usd, 0)) AS utxo_realcap_3y_5y,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 28 * 12 * 5
         AND DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) < 28 * 12 * 8,
         txo.output_cost_basis_usd, 0)) AS utxo_realcap_5y_8y,
  SUM(IF(DATETIME_DIFF(blocks.block_ts, txo.created_block_ts, DAY) >= 28 * 12 * 8,
         txo.output_cost_basis_usd, 0)) AS utxo_realcap_greater_8y
         
FROM
  blocks
CROSS JOIN
  txo
WHERE
  -- Only include transactions that were created on or after the given block
  blocks.block_number >= txo.created_block_number
  -- Only include transactions there were unspent as of the given block
  AND (
    -- Transactions that are spent after the given block, so they are included
    blocks.block_number < txo.destroyed_block_number
    -- Transactions that are never spent, so they are included
    OR txo.destroyed_block_number IS NULL)
GROUP BY
  date, block_number, block_ts, price_usd
ORDER BY
  date ASC;
'''

In [7]:
print(QUERY)


WITH

-- Outputs subquery: contains relevant information about a given output.
-- A TXO is created when it is an output of a transaction, so this contains
-- metadata about the TXO creation
output AS (
  SELECT
    transactions.HASH AS transaction_hash,
    transactions.block_number AS created_block_number,
    transactions.block_timestamp AS created_block_ts,
    outputs.index AS output_index,
    outputs.value AS output_value
  FROM
    `bigquery-public-data.crypto_bitcoin.transactions` AS transactions,
    transactions.outputs AS outputs
    ),

-- Inputs subquery: contains relevant information about a given input.
-- A TXO is consumed when it is the input to a transaction, so this metadata
-- tells us about when a TXO is spent or destroyed
input AS (
  SELECT
    transactions.hash AS spending_transaction_hash,
    inputs.spent_transaction_hash AS spent_transaction_hash,
    transactions.block_number AS destroyed_block_number,
    transactions.block_timestamp AS destroyed_block_ts,

That is our full query to get the HODL waves & Realized Cap data!

I recommend copy/pasting the query into the [BigQuery web UI](https://bigquery.cloud.google.com/) and running from there. You can also run the query from this notebook using [Pandas BigQuery API](https://pandas-gbq.readthedocs.io/en/latest/install.html) if desired. Be sure to set the query dialect to Standard SQL.

The query takes ~50 minutes to run, and when it's done you'll have a time series with the HODL waves distribution. You can then save the query output as a CSV, which we'll now be loading into the notebook and plotting.

In [8]:
import pandas as pd
import numpy as np
import os

%load_ext autoreload
%autoreload 2
%config InlineBackend.figure_format = 'retina'

import chart_utils

In [9]:
# Save your own version of the HODL waves query output, or use the version from the repo
waves = pd.read_csv("./data/hodl_waves_real_cap.csv")
# Load in CoinMetrics BTC data to get daily price
price = pd.read_csv("btc.csv",
                    usecols=['date', 'PriceUSD', 'SplyCur', 'CapRealUSD'])
# Join the price data onto the waves dataframe
waves = waves.merge(price, on='date')

# dates = pd.date_range(
#     start=np.min(waves['date']),
#     end='2024-05-01').strftime('%Y-%m-%d')

# date_df = pd.DataFrame(dates, columns=['date'])

# waves = date_df.merge(waves, on='date', how='left').reset_index(drop=True)
# waves.columns.values

In [10]:
print(waves.columns.values)
waves.head()

['date' 'block_number' 'block_ts' 'price_usd' 'total_utxo_value'
 'utxo_value_under_1d' 'utxo_value_1d_1w' 'utxo_value_1w_1m'
 'utxo_value_1m_3m' 'utxo_value_3m_6m' 'utxo_value_6m_12m'
 'utxo_value_12m_18m' 'utxo_value_18m_24m' 'utxo_value_2y_3y'
 'utxo_value_3y_5y' 'utxo_value_5y_8y' 'utxo_value_greater_8y'
 'total_utxo_count' 'utxo_count_under_1d' 'utxo_count_1d_1w'
 'utxo_count_1w_1m' 'utxo_count_1m_3m' 'utxo_count_3m_6m'
 'utxo_count_6m_12m' 'utxo_count_12m_18m' 'utxo_count_18m_24m'
 'utxo_count_2y_3y' 'utxo_count_3y_5y' 'utxo_count_5y_8y'
 'utxo_count_greater_8y' 'total_utxo_count_filter'
 'utxo_count_filter_under_1d' 'utxo_count_filter_1d_1w'
 'utxo_count_filter_1w_1m' 'utxo_count_filter_1m_3m'
 'utxo_count_filter_3m_6m' 'utxo_count_filter_6m_12m'
 'utxo_count_filter_12m_18m' 'utxo_count_filter_18m_24m'
 'utxo_count_filter_2y_3y' 'utxo_count_filter_3y_5y'
 'utxo_count_filter_5y_8y' 'utxo_count_filter_greater_8y' 'realized_cap'
 'utxo_realcap_under_1d' 'utxo_realcap_1d_1w' 'utxo_r

date  block_number             block_ts  price_usd  total_utxo_value  \
0  2009-01-03             0  2009-01-03T18:15:05        NaN        5000000000   
1  2009-01-09            14  2009-01-09T04:33:09        NaN       75000000000   
2  2009-01-10            75  2009-01-10T23:57:02        NaN      380000000000   
3  2009-01-11           168  2009-01-11T23:39:41        NaN      845000000000   
4  2009-01-12           262  2009-01-12T23:45:47        NaN     1315000000000   

   utxo_value_under_1d  utxo_value_1d_1w  utxo_value_1w_1m  utxo_value_1m_3m  \
0           5000000000                 0                 0                 0   
1          70000000000        5000000000                 0                 0   
2         305000000000       70000000000        5000000000                 0   
3         465000000000      375000000000        5000000000                 0   
4         475000000000      835000000000        5000000000                 0   

   utxo_value_3m_6m  ...  utxo_realcap_6m_12m  utxo_realcap_12m_18m  \
0                 0  ...                  0.0                   0.0   
1                 0  ...                  0.0                   0.0   
2                 0  ...                  0.0                   0.0   
3                 0  ...                  0.0                   0.0   
4                 0  ...                  0.0                   0.0   

   utxo_realcap_18m_24m  utxo_realcap_2y_3y  utxo_realcap_3y_5y  \
0                   0.0                 0.0                 0.0   
1                   0.0                 0.0                 0.0   
2                   0.0                 0.0                 0.0   
3                   0.0                 0.0                 0.0   
4                   0.0                 0.0                 0.0   

   utxo_realcap_5y_8y  utxo_realcap_greater_8y  CapRealUSD  PriceUSD  SplyCur  
0                 0.0                      0.0         0.0       NaN      0.0  
1                 0.0                      0.0         0.0       NaN    950.0  
2                 0.0                      0.0         0.0       NaN   4000.0  
3                 0.0                      0.0         0.0       NaN   8650.0  
4                 0.0                      0.0         0.0       NaN  13350.0  

[5 rows x 59 columns]

In [11]:
# Since our UTXO value columns are denominated in Sats, we must dived by 100M to get to BTC.
waves['OurCapRealUSD'] = waves['realized_cap'] / 100000000
waves['CapRealUSDDelta'] = waves['OurCapRealUSD'] - waves['CapRealUSD']

In [12]:
waves[:-5]

date  block_number             block_ts    price_usd  \
0     2009-01-03             0  2009-01-03T18:15:05          NaN   
1     2009-01-09            14  2009-01-09T04:33:09          NaN   
2     2009-01-10            75  2009-01-10T23:57:02          NaN   
3     2009-01-11           168  2009-01-11T23:39:41          NaN   
4     2009-01-12           262  2009-01-12T23:45:47          NaN   
...          ...           ...                  ...          ...   
4128  2020-04-28        628069  2020-04-28T23:58:41  7769.899698   
4129  2020-04-29        628214  2020-04-29T23:57:19  8761.837170   
4130  2020-04-30        628349  2020-04-30T23:51:29  8652.410991   
4131  2020-05-01        628490  2020-05-01T23:57:03  8855.535258   
4132  2020-05-02        628638  2020-05-02T23:54:28  8977.281705   

      total_utxo_value  utxo_value_under_1d  utxo_value_1d_1w  \
0           5000000000           5000000000                 0   
1          75000000000          70000000000        5000000000   
2         380000000000         305000000000       70000000000   
3         845000000000         465000000000      375000000000   
4        1315000000000         475000000000      835000000000   
...                ...                  ...               ...   
4128  1835084604497096       17787723376695    61609205309658   
4129  1835265854497096       58052908653375    38776470770832   
4130  1835434604497096       39957742165343    65516500194182   
4131  1835610854497096       25563234682961    81520855573872   
4132  1835795854497096       13633244294282    94254003313566   

      utxo_value_1w_1m  utxo_value_1m_3m  utxo_value_3m_6m  ...  \
0                    0                 0                 0  ...   
1                    0                 0                 0  ...   
2           5000000000                 0                 0  ...   
3           5000000000                 0                 0  ...   
4           5000000000                 0                 0  ...   
...                ...               ...               ...  ...   
4128    81081427792576   209113110168379   116602802687063  ...   
4129    69287280797871   205500758369933   115197289954471  ...   
4130    65179883451402   197268070249755   119439691744761  ...   
4131    64364763305075   190367292288791   124522102987656  ...   
4132    63726079265639   178762383032888   135809112245572  ...   

      utxo_realcap_18m_24m  utxo_realcap_2y_3y  utxo_realcap_3y_5y  \
0             0.000000e+00        0.000000e+00        0.000000e+00   
1             0.000000e+00        0.000000e+00        0.000000e+00   
2             0.000000e+00        0.000000e+00        0.000000e+00   
3             0.000000e+00        0.000000e+00        0.000000e+00   
4             0.000000e+00        0.000000e+00        0.000000e+00   
...                    ...                 ...                 ...   
4128          8.131426e+09        2.563489e+10        1.353079e+09   
4129          8.099043e+09        2.559505e+10        1.361068e+09   
4130          8.074467e+09        2.557560e+10        1.373879e+09   
4131          8.074719e+09        2.553212e+10        1.410440e+09   
4132          8.068778e+09        2.548175e+10        1.467005e+09   

      utxo_realcap_5y_8y  utxo_realcap_greater_8y    CapRealUSD     PriceUSD  \
0           0.000000e+00             0.000000e+00  0.000000e+00          NaN   
1           0.000000e+00             0.000000e+00  0.000000e+00          NaN   
2           0.000000e+00             0.000000e+00  0.000000e+00          NaN   
3           0.000000e+00             0.000000e+00  0.000000e+00          NaN   
4           0.000000e+00             0.000000e+00  0.000000e+00          NaN   
...                  ...                      ...           ...          ...   
4128        5.650801e+08             5.462462e+06  1.015432e+11  7769.899698   
4129        5.652730e+08             5.466884e+06  1.023404e+11  8761.837170   
4130        5.654957e+08             5.471086e+0

In [13]:
chart_utils.two_axis_chart(
    waves[:-5], x_series='date', y1_series=['OurCapRealUSD', 'CapRealUSD'], y2_series='CapRealUSDDelta',
    title='Our calculated Realized Vap vs CoinMetrics', 
    y1_series_axis_type='linear',
    y2_series_axis_type='linear', y2_series_axis_format="{n}")

In [17]:
chart_utils.hodl_waves_chart(waves.dropna(), version='realcap')

In [15]:
waves

date  block_number             block_ts    price_usd  \
0     2009-01-03             0  2009-01-03T18:15:05          NaN   
1     2009-01-09            14  2009-01-09T04:33:09          NaN   
2     2009-01-10            75  2009-01-10T23:57:02          NaN   
3     2009-01-11           168  2009-01-11T23:39:41          NaN   
4     2009-01-12           262  2009-01-12T23:45:47          NaN   
...          ...           ...                  ...          ...   
4133  2020-05-03        628806  2020-05-03T23:59:35  8896.795638   
4134  2020-05-04        628964  2020-05-04T23:57:26  8881.954305   
4135  2020-05-05        629122  2020-05-05T23:55:18  8985.879599   
4136  2020-05-06        629276  2020-05-06T23:51:39  9266.813073   
4137  2020-05-07        629423  2020-05-07T23:49:50  9993.753177   

      total_utxo_value  utxo_value_under_1d  utxo_value_1d_1w  \
0           5000000000           5000000000                 0   
1          75000000000          70000000000        5000000000   
2         380000000000         305000000000       70000000000   
3         845000000000         465000000000      375000000000   
4        1315000000000         475000000000      835000000000   
...                ...                  ...               ...   
4133  1836005854497096       24363177701171    83865478709090   
4134  1836203354497096       19599077785331    87785356432753   
4135  1836400854497096       29798988032248    77052571265483   
4136  1836593354497096       25877444664010    67270673244847   
4137  1836777104497096       42738732012796    45995386862975   

      utxo_value_1w_1m  utxo_value_1m_3m  utxo_value_3m_6m  ...  \
0                    0                 0                 0  ...   
1                    0                 0                 0  ...   
2           5000000000                 0                 0  ...   
3           5000000000                 0                 0  ...   
4           5000000000                 0                 0  ...   
...                ...               ...               ...  ...   
4133    63678500849532   178414507777504   136458122584361  ...   
4134    63848195081954   178603470368792   135408157714928  ...   
4135    62405189255213   177778850932082   137038902388374  ...   
4136    79196938615541   176265189749745   136086222803312  ...   
4137    89813436730567   174452846983052   134900710141625  ...   

      utxo_realcap_18m_24m  utxo_realcap_2y_3y  utxo_realcap_3y_5y  \
0             0.000000e+00        0.000000e+00        0.000000e+00   
1             0.000000e+00        0.000000e+00        0.000000e+00   
2             0.000000e+00        0.000000e+00        0.000000e+00   
3             0.000000e+00        0.000000e+00        0.000000e+00   
4             0.000000e+00        0.000000e+00        0.000000e+00   
...                    ...                 ...                 ...   
4133          8.066759e+09        2.535943e+10        1.570387e+09   
4134          8.040204e+09        2.528963e+10        1.665959e+09   
4135          8.055320e+09        2.528708e+10        1.685224e+09   
4136          8.044150e+09        2.527505e+10        1.708429e+09   
4137          8.046070e+09        2.522223e+10        1.740050e+09   

      utxo_realcap_5y_8y  utxo_realcap_greater_8y    CapRealUSD     PriceUSD  \
0           0.000000e+00             0.000000e+00  0.000000e+00          NaN   
1           0.000000e+00             0.000000e+00  0.000000e+00          NaN   
2           0.000000e+00             0.000000e+00  0.000000e+00          NaN   
3           0.000000e+00             0.000000e+00  0.000000e+00          NaN   
4           0.000000e+00             0.000000e+00  0.000000e+00          NaN   
...                  ...                      ...           ...          ...   
4133        5.657452e+08             5.494340e+06  1.029659e+11  8896.795638   
4134        5.659150e+08             5.497646e+06  1.030642e+11  8881.954305   
4135        5.659850e+08             5.507644e+0